In [23]:
!git clone https://github.com/DarkLord0206/texture.git

fatal: destination path 'texture' already exists and is not an empty directory.


In [ ]:
!pip install datasets transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 362 kB 33.5 MB/s 
     |████████████████████████████████| 4.4 MB 56.7 MB/s 
     |████████████████████████████████| 140 kB 75.9 MB/s 
     |████████████████████████████████| 212 kB 71.3 MB/s 
     |████████████████████████████████| 1.1 MB 59.9 MB/s 
     |████████████████████████████████| 101 kB 9.0 MB/s 
     |████████████████████████████████| 596 kB 62.1 MB/s 
     |████████████████████████████████| 127 kB 78.6 MB/s 
     |████████████████████████████████| 6.6 MB 47.5 MB/s 
     |████████████████████████████████| 94 kB 3.7 MB/s 
     |████████████████████████████████| 271 kB 75.0 MB/s 
     |████████████████████████████████| 144 kB 76.3 MB/s 
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3
  Attempting uninstall: pyyaml
    Found existing

In [ ]:
from datasets import load_dataset,DatasetDict,Dataset,load_metric
import numpy as np
from transformers import AutoFeatureExtractor
from torchvision.transforms import RandomResizedCrop, Compose, Normalize, ToTensor

In [ ]:
dataset = load_dataset("imagefolder", data_dir="/content/texture/KTH-TIPS2-b/")
metric=load_metric("accuracy")

Resolving data files:   0%|          | 0/4335 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/417 [00:00<?, ?it/s]

Using custom data configuration default-bf4c7e823263ad61


Extracting data files: 0it [00:00, ?it/s]

Extracting data files: 0it [00:00, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Dataset imagefolder downloaded and prepared to /root/.cache/huggingface/datasets/imagefolder/default-bf4c7e823263ad61/0.0.0/48efdc62d40223daee675ca093d163bcb6cb0b7d7f93eb25aebf5edca72dc597. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [ ]:
labels = dataset["train"].features["label"].names
label2id, id2label = dict(), dict()
for i, label in enumerate(labels):
    label2id[label] = str(i)
    id2label[str(i)] = label

In [ ]:
feature_extractor = AutoFeatureExtractor.from_pretrained("google/vit-base-patch16-224-in21k")

Downloading:   0%|          | 0.00/160 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/502 [00:00<?, ?B/s]

In [ ]:
from torchvision.transforms import (
    CenterCrop,
    Compose,
    Normalize,
    RandomHorizontalFlip,
    RandomResizedCrop,
    Resize,
    ToTensor,
)

normalize = Normalize(mean=feature_extractor.image_mean, std=feature_extractor.image_std)
train_transforms = Compose(
        [
            RandomResizedCrop(feature_extractor.size),
            RandomHorizontalFlip(),
            ToTensor(),
            normalize,
        ]
    )

val_transforms = Compose(
        [
            Resize(feature_extractor.size),
            CenterCrop(feature_extractor.size),
            ToTensor(),
            normalize,
        ]
    )

def preprocess_train(example_batch):
    """Apply train_transforms across a batch."""
    example_batch["pixel_values"] = [
        train_transforms(image.convert("RGB")) for image in example_batch["image"]
    ]
    return example_batch

def preprocess_val(example_batch):
    """Apply val_transforms across a batch."""
    example_batch["pixel_values"] = [val_transforms(image.convert("RGB")) for image in example_batch["image"]]
    return example_batch

In [ ]:
train=dataset["train"]

In [ ]:
val=dataset['test']

In [ ]:
train.set_transform(preprocess_train)
val.set_transform(preprocess_val)

Parameter 'transform'=<function preprocess_train at 0x7fd595e23dd0> of the transform datasets.arrow_dataset.Dataset.set_format couldn't be hashed properly, a random hash was used instead. Make sure your transforms and parameters are serializable with pickle or dill for the dataset fingerprinting and caching to work. If you reuse this transform, the caching mechanism will consider it to be different from the previous calls and recompute everything. This warning is only showed once. Subsequent hashing failures won't be showed.


In [ ]:
from transformers import AutoModelForImageClassification, TrainingArguments, Trainer

model = AutoModelForImageClassification.from_pretrained(
    "google/vit-base-patch16-224-in21k",
    num_labels=len(labels),
    id2label=id2label,
    label2id=label2id,
    ignore_mismatched_sizes=True
)

Downloading:   0%|          | 0.00/330M [00:00<?, ?B/s]

Some weights of the model checkpoint at google/vit-base-patch16-224-in21k were not used when initializing ViTForImageClassification: ['pooler.dense.bias', 'pooler.dense.weight']
- This IS expected if you are initializing ViTForImageClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ViTForImageClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ViTForImageClassification were not initialized from the model checkpoint at google/vit-base-patch16-224-in21k and are newly initialized: ['classifier.weight', 'classifier.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
args = TrainingArguments(
    "ViTFineTuned",
    remove_unused_columns=False,
    evaluation_strategy = "epoch",
    save_strategy = "epoch",
    learning_rate=5e-4,
    per_device_train_batch_size=16,
    gradient_accumulation_steps=4,
    per_device_eval_batch_size=16,
    num_train_epochs=15,
    warmup_ratio=0.1,
    logging_steps=10,
    load_best_model_at_end=True,
    metric_for_best_model="accuracy",
    push_to_hub=True,
)

In [ ]:
import numpy as np

# the compute_metrics function takes a Named Tuple as input:
# predictions, which are the logits of the model as Numpy arrays,
# and label_ids, which are the ground-truth labels as Numpy arrays.
def compute_metrics(eval_pred):
    """Computes accuracy on a batch of predictions"""
    predictions = np.argmax(eval_pred.predictions, axis=1)
    return metric.compute(predictions=predictions, references=eval_pred.label_ids)

In [ ]:
import torch

def collate_fn(examples):
    pixel_values = torch.stack([example["pixel_values"] for example in examples])
    labels = torch.tensor([example["label"] for example in examples])
    return {"pixel_values": pixel_values, "labels": labels}

In [ ]:
trainer = Trainer(
    model,
    args,
    train_dataset=train,
    eval_dataset=val,
    tokenizer=feature_extractor,
    compute_metrics=compute_metrics,
    data_collator=collate_fn,
)

Cloning https://huggingface.co/pthpth/ViTFineTuned into local empty directory.


In [ ]:
train_results = trainer.train()
# rest is optional but nice to have
trainer.save_model()
trainer.log_metrics("train", train_results.metrics)
trainer.save_metrics("train", train_results.metrics)
trainer.save_state()

/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,
***** Running training *****
  Num examples = 4335
  Num Epochs = 15
  Instantaneous batch size per device = 16
  Total train batch size (w. parallel, distributed & accumulation) = 64
  Gradient Accumulation steps = 4
  Total optimization steps = 1005


***** Running Evaluation *****
  Num examples = 417
  Batch size = 16
Saving model checkpoint to ViTFineTuned/checkpoint-67
Configuration saved in ViTFineTuned/checkpoint-67/config.json
Model weights saved in ViTFineTuned/checkpoint-67/pytorch_model.bin
Feature extractor saved in ViTFineTuned/checkpoint-67/preprocessor_config.json
Feature extractor saved in ViTFineTuned/preprocessor_config.json
***** Running Evaluation *****
  Num examples = 417
  Batch size = 16
Saving model checkpoint to ViTFineTuned/checkpoint-134
Configuration saved in ViTFineTuned/checkpoint-134/config.json
Model weights saved in ViTFineTuned/checkpoint-134/pytorch_model.bin
Feature extractor saved in ViTFineTuned/checkpoint-134/preprocessor_config.json
***** Running Evaluation *****
  Num examples = 417
  Batch size = 16
Saving model checkpoint to ViTFineTuned/checkpoint-201
Configuration saved in ViTFineTuned/checkpoint-201/config.json
Model weights saved in ViTFineTuned/checkpoint-201/pytorch_model.bin
Feature 

Upload file pytorch_model.bin:   0%|          | 3.34k/327M [00:00<?, ?B/s]

Upload file runs/Jul15_08-20-36_69b1e7626d29/events.out.tfevents.1657873327.69b1e7626d29.72.0:  14%|#3        …

To https://huggingface.co/pthpth/ViTFineTuned
   225d346..ceb6e7d  main -> main

To https://huggingface.co/pthpth/ViTFineTuned
   ceb6e7d..fe3f66e  main -> main



***** train metrics *****
  epoch                    =        14.99
  total_flos               = 4689843084GF
  train_loss               =       0.1305
  train_runtime            =   0:42:00.45
  train_samples_per_second =       25.799
  train_steps_per_second   =        0.399


In [ ]:
metrics = trainer.evaluate()
# some nice to haves:
trainer.log_metrics("eval", metrics)
trainer.save_metrics("eval", metrics)

***** Running Evaluation *****
  Num examples = 417
  Batch size = 16


***** eval metrics *****
  epoch                   =      14.99
  eval_accuracy           =        1.0
  eval_loss               =     0.0075
  eval_runtime            = 0:00:06.68
  eval_samples_per_second =     62.341
  eval_steps_per_second   =      4.036


In [ ]:
trainer.push_to_hub()

Saving model checkpoint to ViTFineTuned
Configuration saved in ViTFineTuned/config.json
Model weights saved in ViTFineTuned/pytorch_model.bin
Feature extractor saved in ViTFineTuned/preprocessor_config.json


Upload file runs/Jul15_08-20-36_69b1e7626d29/events.out.tfevents.1657876260.69b1e7626d29.72.2: 100%|##########…

To https://huggingface.co/pthpth/ViTFineTuned
   fe3f66e..84ee137  main -> main

To https://huggingface.co/pthpth/ViTFineTuned
   84ee137..4353a35  main -> main



'https://huggingface.co/pthpth/ViTFineTuned/commit/84ee1375ba810a816ec995c09c1cb2b11632eb39'

Login successful
Your token has been saved to /root/.huggingface/token
Authenticated through git-credential store but this isn't the helper defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub. Run the following command in your terminal in case you want to set this credential helper as the default

git config --global credential.helper store
